In [2]:
import numpy as np

from keras.preprocessing.text import Tokenizer, one_hot
from keras.preprocessing.sequence import pad_sequences
from keras.layers import Embedding, Input, LSTM, RepeatVector, Dense, Dropout
from keras.models import Model
import pandas as pd
from nltk.tokenize import word_tokenize 
import gensim
from nltk.corpus import stopwords 
from string import punctuation
from nltk.stem import WordNetLemmatizer
import nltk

nltk.download('punkt')
nltk.download('wordnet')

Using TensorFlow backend.
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\irina\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\irina\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

# Load data

In [3]:
data_file = 'D:/Datasets/amazon_reviews/Video_Games_5.json'
df = pd.read_json(data_file, lines = True)
df.head(2)

asin  helpful  overall  \
0  0700099867  [8, 12]        1   
1  0700099867   [0, 0]        4   

                                          reviewText   reviewTime  \
0  Installing the game was a struggle (because of...   07 9, 2012   
1  If you like rally cars get this game you will ...  06 30, 2013   

       reviewerID                        reviewerName  \
0  A2HD75EMZR8QLN                                 123   
1  A3UR8NLLY1ZHCX  Alejandro Henao "Electronic Junky"   

                                    summary  unixReviewTime  
0  Pay to unlock content? I don't think so.      1341792000  
1                           Good rally game      1372550400

# Preprocess Data

In [4]:
review_data = df.reviewText.values
review_data.size

231780

In [13]:
def custom_tokenizer(nlp):
    prefix_re = spacy.util.compile_prefix_regex(nlp.Defaults.prefixes)
    suffix_re = spacy.util.compile_suffix_regex(nlp.Defaults.suffixes)
    custom_infixes = ['\.\.\.+', '(?<=[0-9])-(?=[0-9])', '[!&:,()]']
    infix_re = spacy.util.compile_infix_regex(custom_infixes)

    tokenizer = spacy.tokenizer.Tokenizer(nlp.vocab,
                                        nlp.Defaults.tokenizer_exceptions,
                                        prefix_re.search,
                                        suffix_re.search,
                                        infix_re.finditer,
                                        token_match=None)
    return lambda text: tokenizer(text)

def process_data_with_spacy(review_data):
    import spacy 
    nlp = spacy.load('en_core_web_sm')
    return [text_to_seq(s, nlp) for s in review_data]

def text_to_seq (s, nlp):
    doc = nlp(s)
    tokens = []
    for tok in doc:
        if not tok.is_stop and not tok.is_punct and not tok.like_url:
            tokens.append(tok.lemma_.lower().strip() if tok.lemma_ != '-PRON-' else tok.lower_)
    return tokens

def text_to_text(s, nlp):
    return ' '.join(text_to_seq(s, nlp))

def process_data_with_spacy_df(df):
    import spacy 
    nlp = spacy.load('en_core_web_sm')
    df['reviewTextProc'] = df.apply (lambda row: text_to_text(row['reviewText'], nlp), axis=1)
    return df


In [14]:
process_data_with_spacy(["I love the beautiful car, my dear. But not, groom!My dear."])

[['i', 'love', 'beautiful', 'car', 'dear', 'but', 'groom!my', 'dear']]

In [8]:
def process_data_with_nltk(review_data):
    stop_words = set(stopwords.words('english')) 
    stop_word_punct = set(stopwords.words('english') + list(punctuation))
    lemmatizer = WordNetLemmatizer()

    review_data_sequenced = []
    for s in review_data:
        word_tokens = word_tokenize(s.lower())
        no_stop_words = [lemmatizer.lemmatize(word) for word in word_tokens if word not in stop_word_punct]
        review_data_sequenced.append(no_stop_words)
    return review_data_sequenced

In [9]:
process_data_with_nltk(["I love the beautiful car,my dear.But not. gr!my"])

[['love', 'beautiful', 'car', 'dear.but', 'gr']]

In [16]:
df = process_data_with_spacy_df(df)
df.head(10)

asin   helpful  overall  \
0  0700099867   [8, 12]        1   
1  0700099867    [0, 0]        4   
2  0700099867    [0, 0]        1   
3  0700099867   [7, 10]        3   
4  0700099867    [2, 2]        4   
5  0700099867    [0, 0]        4   
6  0700099867  [11, 13]        5   
7  0700099867    [1, 4]        1   
8  0700099867    [0, 1]        4   
9  0700099867    [1, 1]        2   

                                          reviewText   reviewTime  \
0  Installing the game was a struggle (because of...   07 9, 2012   
1  If you like rally cars get this game you will ...  06 30, 2013   
2  1st shipment received a book instead of the ga...  06 28, 2014   
3  I got this version instead of the PS3 version,...  09 14, 2011   
4  I had Dirt 2 on Xbox 360 and it was an okay ga...  06 14, 2011   
5  Overall this is a well done racing game, with ...  05 11, 2013   
6  Loved playing Dirt 2 and I thought the graphic...  08 14, 2011   
7  I can't tell you what a piece of dog**** this ...  11 24, 2012   
8  I initially gave this one star because it was ...  11 14, 2012   
9  I still haven't figured this one out. Did ever...   02 8, 2014   

       reviewerID                        reviewerName  \
0  A2HD75EMZR8QLN                                 123   
1  A3UR8NLLY1ZHCX  Alejandro Henao "Electronic Junky"   
2  A1INA0F5CWW3J4          Amazon Shopper "Mr.Repsol"   
3  A1DLMTOTHQ4AST                            ampgreen   
4  A361M14PU2GUEG        Angry Ryan "Ryan A. Forrest"   
5  A2UTRVO4FDCBH6                              A.R.G.   
6   AN3YYDZAS3O1Y                                 Bob   
7   AQTC623NCESZW                       Chesty Puller   
8  A1QJJU33VNC4S7                              D@rkFX   
9  A2JLT2WY0F2HVI                       D. Sweetapple   

                                             summary  unixReviewTime  \
0           Pay to unlock content? I don't think so.      1341792000   
1                                    Good rally game      1372550400   
2                                          Wrong key      1403913600   
3    awesome game, if it did not crash frequently !!      1315958400   
4                                             DIRT 3      1308009600   
5  Good racing game, terrible Windows Live Requir...      1368230400   
6        A step up from Dirt 2 and that is terrific!      1313280000   
7              Crash 3 is correct name AKA Microsoft      1353715200   
8  A great game ruined by Microsoft's account man...      1352851200   
9                      Couldn't get this one to work      1391817600   

                                      reviewTextProc  
0  instal game struggle game window live bugs).so...  
1  if like rally car game fun it orient 34;europe...  
2  1st shipment receive book instead game.2nd shi...  
3  i get version instead ps3 version turn mistake...  
4  i dirt 2 xbox 360 okay game i start play game ...  
5  overall racing game good graphic time period m...  
6  love play dirt 2 i think graphic good  purchas...  
7  i not tell piece dog game like microsoft makes...  
8  i initially give star crash constantly i recen...  
9  i not figure do instruct game instal strange s...

In [17]:
df.to_json('D:/Datasets/amazon_reviews/Video_Games_5_proc.json')

In [21]:
df_1 = pd.read_json('D:/Datasets/amazon_reviews/Video_Games_5_proc.json')

In [23]:
df_1.shape

(231780, 10)

In [13]:
tokenizer = Tokenizer(filters='!"#$%&()*+,-./:;<=>?@[\\]^_`{|}~\t\n') # nb_words=MAX_NB_WORDS
tokenizer.fit_on_texts(review_data_sequenced)
review_sequences = tokenizer.texts_to_sequences(review_data_sequenced)

In [14]:
print(len(review_sequences))
print(review_sequences[1])

231780
[30, 8, 3329, 160, 1, 14, 11, 2298, 108441, 43770, 2158, 6, 228, 3329, 70, 380, 115, 3801, 161, 1, 108442, 3215, 5, 134, 6, 9, 42, 423]


In [15]:
word_index = tokenizer.word_index
print('Found %s unique tokens.' % len(word_index))
print('Indexes of common words: you = %s, the = %s, it = %s.' % (word_index['you'], word_index['the'], word_index['it']))

Found 369125 unique tokens.
Indexes of common words: you = 16, the = 5, it = 11.


In [1]:
list(word_index.items())[0:10]

NameError: name 'word_index' is not defined

# Model

In [9]:
x_train = pad_sequences(review_sequences)
print(len(x_train[0]))
print(len(x_train[100]))

5940
5940


In [38]:
x_train[0].shape

(5940,)

In [24]:
print('Shape of data tensor:', x_train.shape)

Shape of data tensor: (231780, 5940)


In [35]:
def batch_generator(x, y, batch_size=16):
    
    while True:
        # choose batch_size random images / labels from the data
        idx = np.random.randint(0, x.shape[0], batch_size)
        yield x[idx], tokenizer.texts_to_matrix(y[idx], mode='binary')

In [19]:
# Loading Word2Vec
model = gensim.models.KeyedVectors.load_word2vec_format('D:/Datasets/word2vec/GoogleNews-vectors-negative300.bin', binary=True)

In [20]:
EMBEDDING_DIM = 300
embedding_matrix = np.zeros((len(word_index) + 1, EMBEDDING_DIM))

for word, i in word_index.items():
    if word in model:
        embedding_matrix[i] = model[word]
    else:
        print("Missed word: %s" % word)
        embedding_matrix[i] = np.random.rand(1, EMBEDDING_DIM)[0]

Missed word: infruriating
Missed word: storyonce
Missed word: deathmatchplunderteam
Missed word: stayle
Missed word: offspring's
Missed word: hddvd
Missed word: 8weapons
Missed word: editionwas
Missed word: oldpaul
Missed word: gadgetsso
Missed word: x5info
Missed word: figurethe
Missed word: warriorsherc's
Missed word: optionsbetter
Missed word: rammones
Missed word: sloooooowly
Missed word: tiramies
Missed word: 'return
Missed word: bot'
Missed word: 2002's
Missed word: amaerica
Missed word: playinggameplay
Missed word: r1l2
Missed word: aparrot
Missed word: 10skills
Missed word: 'fix'
Missed word: moneykill
Missed word: willowspringsmost
Missed word: thingsqb
Missed word: 'arcania'
Missed word: peak'
Missed word: xb360's
Missed word: againnot
Missed word: kamitani's
Missed word: fantasticon
Missed word: overll
Missed word: iogear
Missed word: clonky
Missed word: tlj
Missed word: saveconslike
Missed word: naother
Missed word: binks
Missed word: antoinetta
Missed word: enjoing
Missed 

Missed word: tracks'
Missed word: 10touch
Missed word: mtv's
Missed word: uptekken
Missed word: gamns
Missed word: numpad1
Missed word: quiso
Missed word: locationswide
Missed word: competetor
Missed word: criteria'
Missed word: leibnitz
Missed word: easymy
Missed word: verdictatlus
Missed word: mbcons
Missed word: ptoblem
Missed word: spinner24
Missed word: reminesnt
Missed word: personthe
Missed word: woulded
Missed word: copypasted
Missed word: estopolis
Missed word: maneuversoverall
Missed word: merriweather
Missed word: blackflag
Missed word: genesis'
Missed word: 48
Missed word: shoeboxed
Missed word: mercyor
Missed word: bouyght
Missed word: solidinstallment
Missed word: uematsu
Missed word: galunet
Missed word: pyramat
Missed word: largeer
Missed word: nyx
Missed word: nowpros
Missed word: patformer
Missed word: il2
Missed word: undoubtebly
Missed word: microgear
Missed word: eagles'
Missed word: gognitti
Missed word: dsc's
Missed word: dungeonsvendable
Missed word: conspirousy

Missed word: replayabilitycons
Missed word: mvsdk
Missed word: superstylin'
Missed word: winfrey
Missed word: anticts
Missed word: moonberries
Missed word: stathman
Missed word: snowhead
Missed word: thissequel
Missed word: gamesms
Missed word: pulzar
Missed word: usagi
Missed word: mothn
Missed word: valkyria
Missed word: haricut
Missed word: ludicris
Missed word: tvlack
Missed word: whatley
Missed word: ollars
Missed word: final7
Missed word: dogsdogs
Missed word: 3dtvs
Missed word: bhg
Missed word: environmentsremarkable
Missed word: storyine
Missed word: magsec4
Missed word: codesgraphics
Missed word: mastry
Missed word: superroundabout
Missed word: flaot
Missed word: batgrappler
Missed word: steppin'
Missed word: turn10
Missed word: monocolor
Missed word: problemsa
Missed word: feelgreat
Missed word: identifable
Missed word: dingly
Missed word: emulattors
Missed word: 'civilized'
Missed word: transvering
Missed word: bezillions
Missed word: 2ds'
Missed word: fun4
Missed word: stor

Missed word: smallers
Missed word: priferals
Missed word: k65
Missed word: jonury
Missed word: mned
Missed word: trainheaded
Missed word: appealingdifferent
Missed word: 2003with
Missed word: pusher's
Missed word: nruffs
Missed word: andexploring
Missed word: emoci
Missed word: sheong
Missed word: gatcha
Missed word: arena'
Missed word: 'safe'
Missed word: vegas's
Missed word: aurium
Missed word: vthey
Missed word: night1
Missed word: hieronymus
Missed word: x41
Missed word: brutalaty
Missed word: margines
Missed word: weekscons
Missed word: fenrich
Missed word: optionsand
Missed word: itprosleons
Missed word: versionon
Missed word: 'entitlement'
Missed word: inexplicalbly
Missed word: lili
Missed word: sagecraft
Missed word: eant
Missed word: parodius
Missed word: surrounding's
Missed word: mizoguchi
Missed word: brunhilda
Missed word: wzakes
Missed word: satisfing
Missed word: youtbe
Missed word: erxperience
Missed word: mythelogical
Missed word: justitos
Missed word: elderscrolls
Mi

Missed word: 100amazing
Missed word: linelots
Missed word: dependinhg
Missed word: boomshockalaka
Missed word: automaps
Missed word: 'dodge'
Missed word: contstantly
Missed word: androgynousso
Missed word: westren
Missed word: runeys
Missed word: hodgson
Missed word: tasminas
Missed word: reinhard
Missed word: acrcade
Missed word: terrian
Missed word: elemnated
Missed word: hint's
Missed word: precursur
Missed word: 'signal'
Missed word: itsports
Missed word: individualy
Missed word: ingenously
Missed word: beforekillzone
Missed word: steelport
Missed word: deedsmany
Missed word: sticksgood
Missed word: swordsman's
Missed word: 5ecco
Missed word: 20mbps
Missed word: graffcs
Missed word: 5vs5
Missed word: 'ball
Missed word: bnad
Missed word: symbolanyone
Missed word: duvari
Missed word: readerit's
Missed word: dukebots
Missed word: hennesseys
Missed word: aspeccts
Missed word: rednexsurfin'
Missed word: einhander's
Missed word: gunpei
Missed word: aware1
Missed word: shirmishes
Missed w

...

Missed word: frusted
Missed word: scail
Missed word: 9800radeon
Missed word: speedtree
Missed word: centauries
Missed word: modesit
Missed word: fenris
Missed word: openendedness
Missed word: etcbut
Missed word: boldsucceeds
Missed word: whicch
Missed word: activison
Missed word: grrrrrrrrr
Missed word: powes
Missed word: qte'snegatives
Missed word: teamkillers
Missed word: battal
Missed word: fight4
Missed word: worldnow
Missed word: rank's
Missed word: versionfrogger
Missed word: powerment
Missed word: minutes8
Missed word: beinga
Missed word: lucias
Missed word: scoreeasy
Missed word: mediumdynamic
Missed word: 'system'
Missed word: bether
Missed word: mishes
Missed word: replayjust
Missed word: natz
Missed word: midgety
Missed word: sportsgamer's
Missed word: suckssetting
Missed word: modifythus
Missed word: anoher
Missed word: raoh
Missed word: 10amazing
Missed word: scrpit
Missed word: 'door
Missed word: ywhere
Missed word: hesistated
Missed word: gamespotit
Missed word: covenet


Missed word: bounusesmini
Missed word: 280mb
Missed word: giantzeppelin
Missed word: nba2k2
Missed word: moreau
Missed word: gamebeautiful
Missed word: ghelsba
Missed word: boverall
Missed word: destert
Missed word: mhp3rd
Missed word: idiosyncrasy's
Missed word: hillsong
Missed word: credt
Missed word: tryptichon
Missed word: 16s
Missed word: 'tv'
Missed word: kirbyracing
Missed word: levelrunning
Missed word: inpiration
Missed word: assissnated
Missed word: 'forced'
Missed word: carolinas
Missed word: detrimenatl
Missed word: slotsuper
Missed word: droidsadictivelots
Missed word: grinades
Missed word: jerassic
Missed word: uselessand
Missed word: boxhead
Missed word: rigamorole
Missed word: grimlim
Missed word: berserks
Missed word: animade
Missed word: tolove
Missed word: controllersons
Missed word: d3dx9
Missed word: brieflydemon's
Missed word: lorna
Missed word: gamewe
Missed word: bugs3
Missed word: pokemon4
Missed word: smouldering
Missed word: scarredcyanidemy
Missed word: vest

Missed word: b00006i5zx
Missed word: aminkar
Missed word: ricking
Missed word: versasorry
Missed word: awestricken
Missed word: 'euphoria'
Missed word: youpaladin
Missed word: preceders
Missed word: compotable
Missed word: kirkpatrickj
Missed word: tracker'
Missed word: 'openworld'
Missed word: tailtap
Missed word: robonotic
Missed word: ffsp
Missed word: cyberbentically
Missed word: thinkre4'sganados
Missed word: screwish
Missed word: kronc
Missed word: monovours
Missed word: eashl
Missed word: sqeamish
Missed word: 'mists
Missed word: doax2
Missed word: lucien
Missed word: seenes
Missed word: gaben
Missed word: 511
Missed word: polks
Missed word: wolk
Missed word: mongol
Missed word: 1797
Missed word: motherbase
Missed word: cic
Missed word: possibilitiespro
Missed word: regulos
Missed word: gfa3
Missed word: chernenko's
Missed word: shop's
Missed word: 'solve
Missed word: phreak
Missed word: sutble
Missed word: xq'
Missed word: modethat
Missed word: videos'
Missed word: chabert
Miss

Missed word: anb'
Missed word: constantlyof
Missed word: intoone
Missed word: wooooohooo
Missed word: watch4
Missed word: axwell
Missed word: anddead
Missed word: momose
Missed word: 'throwing'
Missed word: katey
Missed word: 'quantity
Missed word: developer's
Missed word: sighta
Missed word: 'beta'
Missed word: 10vii
Missed word: espscially
Missed word: intp
Missed word: pipe16
Missed word: limmited
Missed word: 10standing
Missed word: campaign'
Missed word: vulcans
Missed word: enjolras
Missed word: disintigration
Missed word: extraordinario
Missed word: wheeldoes
Missed word: suck'
Missed word: nordschleife
Missed word: rmp
Missed word: 550lbs
Missed word: monstership
Missed word: piett
Missed word: ''advanced
Missed word: hellpowers
Missed word: myenemy's
Missed word: nintendophils
Missed word: dollar's
Missed word: attches
Missed word: numeroussecrets
Missed word: cxplained
Missed word: mizrabel's
Missed word: commodoties
Missed word: playststation
Missed word: dh1
Missed word: 1g

Missed word: notdisappoint
Missed word: therethe
Missed word: robada
Missed word: nmeed
Missed word: playsstation1
Missed word: directv's
Missed word: maerwen
Missed word: killzones
Missed word: isrest
Missed word: deepby
Missed word: brick's
Missed word: inuyasha's
Missed word: freeforall
Missed word: funni
Missed word: strategty
Missed word: bloaty
Missed word: tnbc
Missed word: carmichael
Missed word: 10integration
Missed word: 'grind'
Missed word: gungans
Missed word: beachwood
Missed word: striderbad
Missed word: 5confusing
Missed word: rog
Missed word: cable4
Missed word: niccolo
Missed word: kaede's
Missed word: 9graphic's
Missed word: nify
Missed word: informada
Missed word: 'hojo
Missed word: xpos
Missed word: whichputs
Missed word: estructure
Missed word: etcgood
Missed word: amiba
Missed word: 'ricochet'
Missed word: kingdomswhich
Missed word: vehicial
Missed word: apropro
Missed word: lookikg
Missed word: 'elements'
Missed word: enivermont
Missed word: aaaahhhhh
Missed word

In [22]:
MAX_SEQUENCE_LENGTH = 5940
embedding_layer = Embedding(len(word_index) + 1,
                                EMBEDDING_DIM,
                                weights=[embedding_matrix],
                                input_length=MAX_SEQUENCE_LENGTH,
                                trainable=False)

In [37]:
input_img = Input(shape=(MAX_SEQUENCE_LENGTH, EMBEDDING_DIM, 1))  # adapt this if using `channels_first` image data format

x = Conv2D(32, (3, 3), activation='relu', padding='same')(input_img)
x = MaxPooling2D((2, 2), padding='same')(x)
x = Conv2D(32, (3, 3), activation='relu', padding='same')(x)
encoded = MaxPooling2D((2, 2), padding='same')(x)

x = Conv2D(32, (3, 3), activation='relu', padding='same')(encoded)
x = UpSampling2D((2, 2))(x)
x = Conv2D(32, (3, 3), activation='relu', padding='same')(x)
x = UpSampling2D((2, 2))(x)
decoded = Conv2D(1, (3, 3), activation='sigmoid', padding='same')(x)

autoencoder = Model(input_img, decoded)
autoencoder.compile(optimizer='adadelta', loss='binary_crossentropy')
    
sequence_autoencoder.fit_generator(generator=batch_generator(x_train, review_data, batch_size = 32),
                                   steps_per_epoch = 2000)

Epoch 1/1
  14/2000 [..............................] - ETA: 21:40:01 - loss: 1372.5281

KeyboardInterrupt: 